In [ ]:
# Install prereqs if needed

!pip install clickhouse-connect -q
!pip install web3 -q

import clickhouse_connect
import pandas as pd
import matplotlib.pyplot as plt
import requests
import plotly.graph_objects as go
from google.colab import data_table
from web3 import Web3
import matplotlib.dates as mdates
import plotly.express as px
from datetime import datetime, timedelta
from google.colab import userdata
import time

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 10.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 14.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.4/1.4 MB 25.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 580.7/580.7 kB 13.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100.5/100.5 kB 3.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.2/49.2 kB 2.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 164.8/164.8 kB 8.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 286.1/286.1 kB 13.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 169.6/169.6 kB 7.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 39.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.4/48.4 kB 2.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.3/2.3 MB 36.2 MB/s eta 0:00:00


In [ ]:
client = clickhouse_connect.get_client(dsn=userdata.get('CLICKHOUSE_DSN'))

In [ ]:
api_key = userdata.get('INFURA_KEY')

# Retrieve the Infura key from userdata
INFURA_URL = f"https://mainnet.infura.io/v3/{api_key}"

# Verify it's stored (you can disable this print statement later)
print(INFURA_URL)

https://mainnet.infura.io/v3/e9cc4361dcb54477ab0dea78bfdfd415


In [ ]:
sy_tokens = client.query_df('''

    SELECT DISTINCT
        inputs.arg0::String as sy_token,
        evm_hex_encode(address) AS sy_token_factory
    FROM
        ethereum_mainnet_decoded_logs
    WHERE
        signature = 'CreateYieldContract(address,uint256,address,address)'
        and
        sy_token_factory in (
            lower('0x35A338522a435D46f77Be32C70E215B813D0e3aC'), -- yieldContractFactoryV5
            lower('0xdF3601014686674e53d1Fa52F7602525483F9122'), -- yieldContractFactoryV3
            lower('0x273b4bFA3Bb30fe8F32c467b5f0046834557F072')  -- yieldContractFactoryV4
        )
''')

data_table.DataTable(sy_tokens, include_index=False, num_rows_per_page=20)

In [ ]:
web3 = Web3(Web3.HTTPProvider(INFURA_URL))

ERC20_ABI = [
    {
        "constant": True,
        "inputs": [],
        "name": "name",
        "outputs": [{"name": "", "type": "string"}],
        "payable": False,
        "stateMutability": "view",
        "type": "function",
    },
    {
        "constant": True,
        "inputs": [],
        "name": "symbol",
        "outputs": [{"name": "", "type": "string"}],
        "payable": False,
        "stateMutability": "view",
        "type": "function",
    },
    {
        "constant": True,
        "inputs": [],
        "name": "decimals",
        "outputs": [{"name": "", "type": "uint8"}],
        "payable": False,
        "stateMutability": "view",
        "type": "function",
    },
    {
        "constant": True,
        "inputs": [],
        "name": "assetInfo",
        "outputs": [
            {"name": "assetType", "type": "uint8"},
            {"name": "assetAddress", "type": "address"},
            {"name": "assetDecimals", "type": "uint8"}
        ],
        "payable": False,
        "stateMutability": "view",
        "type": "function",
    },
]

def fetch_token_details(token_address):
    contract = web3.eth.contract(
        address=Web3.to_checksum_address(token_address),
        abi=ERC20_ABI
    )
    try:
        name = contract.functions.name().call()
    except Exception:
        name = None
    try:
        symbol = contract.functions.symbol().call()
    except Exception:
        symbol = None
    try:
        decimals = contract.functions.decimals().call()
    except Exception:
        decimals = None
    try:
        asset_type, asset_address, asset_decimals = contract.functions.assetInfo().call()
    except Exception:
        asset_type, asset_address, asset_decimals = (None, None, None)
    return name, symbol, decimals, asset_type, asset_address, asset_decimals

# Add token details to the DataFrame
token_details = sy_tokens["sy_token"].apply(fetch_token_details)
sy_tokens["name"], sy_tokens["symbol"], sy_tokens["decimals"], \
sy_tokens["asset_type"], sy_tokens["asset_address"], sy_tokens["asset_decimals"] = zip(*token_details)

In [ ]:
# Convert sy_tokens list to a DataFrame
tokens_df = pd.DataFrame(sy_tokens)

# Remove rows with NaN values
tokens_df_clean = tokens_df.dropna()

# Define the addresses
ZERO_ADDRESS = "0x0000000000000000000000000000000000000000"
WETH_ADDRESS = "0xc02aaa39b223fe8d0a0e5c4f27ead9083c756cc2"
SOLVBTC_ADDRESS = "0xe7c253ead50976caf7b0c2cbca569146a7741b50"
WBTC_ADDRESS = "0x2260fac5e5542a773aa44fbcfedf7c193bc2c599"

# Define a mapping function for asset_address replacement
def map_asset_address(addr):
    addr_lower = addr.lower()
    if addr_lower == ZERO_ADDRESS.lower():
        return WETH_ADDRESS
    elif addr_lower == SOLVBTC_ADDRESS.lower():
        return WBTC_ADDRESS
    else:
        return addr

# Apply the mapping function to asset_address column
tokens_df_clean["asset_address"] = tokens_df_clean["asset_address"].apply(map_asset_address)

<ipython-input-7-2452ee6d44c8>:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  tokens_df_clean["asset_address"] = tokens_df_clean["asset_address"].apply(map_asset_address)


In [ ]:
# Extract unique asset addresses, converting them to lowercase (if required by the API)
unique_asset_addresses = tokens_df_clean["asset_address"].str.lower().unique().tolist()

# Print the unique asset addresses
unique_asset_addresses

['0x04c154b66cb340f3ae24111cc767e0184ed00cc6',
 '0x35fa164735182de50811e8e2e824cfb9b6118ac2',
 '0xc02aaa39b223fe8d0a0e5c4f27ead9083c756cc2',
 '0x2260fac5e5542a773aa44fbcfedf7c193bc2c599',
 '0x4c9edd5852cd905f086c759e8383e09bff1e68b3',
 '0x57e114b691db790c35207b2e685d4a43181e6061',
 '0x77e06c9eccf2e797fd462a92b6d7642ef85b0a44',
 '0xdc035d45d973e3ec169d2276ddab16f1e407384f',
 '0xa0b86991c6218b36c1d19d4a2e9eb0ce3606eb48',
 '0x35d8949372d46b7a3d5a56006ae77b215fc69bc0',
 '0xec53bf9167f50cdeb3ae105f56099aaab9061f83',
 '0x40d16fc0246ad3160ccc09b8d0d3a2cd28ae6c2f',
 '0x657e8c867d8b37dcc18fa4caead9c45eb088c642',
 '0xf939e0a03fb07f59a73314e73794be0e57ac1b4e',
 '0x917cee801a67f933f2e6b33fc0cd1ed2d5909d88',
 '0xbeef69ac7870777598a04b2bd4771c71212e6abc',
 '0x84631c0d0081fde56deb72f6de77abbbf6a9f93a',
 '0x5fd13359ba15a84b76f7f87568309040176167cd',
 '0x7a4effd87c2f3c55ca251080b1343b605f327e3a',
 '0x856c4efb76c1d1ae02e20ceb03a2a6a08b0b8dc3',
 '0x004e9c3ef86bc1ca1f0bb5c7662861ee93350568',
 '0xdac17f958

In [ ]:
def get_liquidity_value(pair):
    liq = pair.get("liquidity", 0)
    if isinstance(liq, dict):
        # If liquidity is a dict, try to get the "usd" value.
        return float(liq.get("usd", 0))
    try:
        return float(liq)
    except Exception:
        return 0

def get_usd_price_dexscreener(asset_address):
    url = f"https://api.dexscreener.com/latest/dex/tokens/{asset_address}"
    try:
        response = requests.get(url)
        response.raise_for_status()  # Check for HTTP errors
        data = response.json()

        pairs = data.get("pairs", [])
        if pairs:
            # Select the pair with the highest liquidity using our helper.
            best_pair = max(pairs, key=get_liquidity_value)
            price_str = best_pair.get("priceUsd", None)
            print(f"Price for {asset_address} (using pair with liquidity {best_pair.get('liquidity')}):", price_str)
            if price_str is not None:
                return float(price_str)
        return None
    except Exception as e:
        print(f"Error fetching price for {asset_address} from Dexscreener: {e}")
        return None

# Create a dictionary to store the fetched USD prices for each unique asset address
usd_prices = {}
for address in unique_asset_addresses:
    price = get_usd_price_dexscreener(address)
    usd_prices[address] = price
    # Delay between requests to reduce the risk of hitting rate limits
    time.sleep(1)

# Map the fetched prices back to the DataFrame.
tokens_df_clean["usd_price"] = tokens_df_clean["asset_address"].str.lower().map(usd_prices)

# Display the updated DataFrame
tokens_df_clean

Price for 0x04c154b66cb340f3ae24111cc767e0184ed00cc6 (using pair with liquidity {'usd': 19725924.62, 'base': 4999.9134, 'quote': 2291.3438}): 2703.72
Price for 0x35fa164735182de50811e8e2e824cfb9b6118ac2 (using pair with liquidity {'usd': 179589.06, 'base': 35.14, 'quote': 33.363}): 2620.87
Price for 0xc02aaa39b223fe8d0a0e5c4f27ead9083c756cc2 (using pair with liquidity {'usd': 172266688.34, 'base': 45159, 'quote': 53592227}): 2627.90
Price for 0x2260fac5e5542a773aa44fbcfedf7c193bc2c599 (using pair with liquidity {'usd': 132093439.47, 'base': 1154.8845, 'quote': 23909660}): 93674.97
Price for 0x4c9edd5852cd905f086c759e8383e09bff1e68b3 (using pair with liquidity {'usd': 103019094.07, 'base': 69106050, 'quote': 34258199}): 0.9954
Price for 0x57e114b691db790c35207b2e685d4a43181e6061 (using pair with liquidity {'usd': 8443102.45, 'base': 10131326, 'quote': 10178429}): 0.4151
Price for 0x77e06c9eccf2e797fd462a92b6d7642ef85b0a44 (using pair with liquidity {'usd': 4493140.62, 'base': 6892.1662,

<ipython-input-9-2e91f7a81436>:40: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  tokens_df_clean["usd_price"] = tokens_df_clean["asset_address"].str.lower().map(usd_prices)


sy_token  \
0    0x440d08d85cb12352dabac2971de81e9be702d239   
1    0xd7df7e085214743530aff339afc420c7c720bfa7   
2    0x34349c5569e7b846c3558961552d2202760a9789   
5    0x9d6ec7a7b051b32205f74b140a0fa6f09d7f223e   
6    0xae754a3b4553ea2ea4794d0171a56ac12fdb2782   
..                                          ...   
115  0x8db42af6b2de9e8aee47f3423570d8e9c3873796   
118  0xca4fe88658073cadafd40045ba1c170a684d6e78   
119  0x248d83f7ac03cebcc06d5c1a52c9b5d0ebb9936e   
120  0x215a61dead7e1303b8571bb429491aeac5f2061e   
121  0x8c28d28bad669afadc37b034a8070d6d7b9dfb74   

                               sy_token_factory                          name  \
0    0xdf3601014686674e53d1fa52f7602525483f9122  SY Autocompounding Pirex ETH   
1    0xdf3601014686674e53d1fa52f7602525483f9122     SY Zircuit Ether.fi weETH   
2    0xdf3601014686674e53d1fa52f7602525483f9122      SY Zircuit Staking rsETH   
5    0x35a338522a435d46f77be32c70e215b813d0e3ac          SY Corn Lombard LBTC   
6    0x35a338522a435d46f77be32c70e215b813d0e3ac        SY Corn Bedrock uniBTC   
..                                          ...                           ...   
115  0x35a338522a435d46f77be32c70e215b813d0e3ac                SY Karak WEETH   
118  0xdf3601014686674e53d1fa52f7602525483f9122                SY Ethena USDe   
119  0xdf3601014686674e53d1fa52f7602525483f9122                SY Ethena USDe   
120  0xdf3601014686674e53d1fa52f7602525483f9122               SY Ethena sUSDE   
121  0xdf3601014686674e53d1fa52f7602525483f9122                      SY aUSDT   

             symbol  decimals  asset_type  \
0         SY-apxETH      18.0         0.0   
1       SY-zs-weETH      18.0         0.0   
2       SY-zs-rsETH      18.0         0.0   
5       SY-cornLBTC       8.0         0.0   
6    SY-corn-uniBTC       8.0         0.0   
..              ...       ...         ...   
115  SY-Karak-WEETH      18.0         0.0   
118         SY-USDe      18.0         0.0   
119         SY-USDe      18.0         0.0   
120        SY-sUSDE      18.0         0.0   
121        SY-aUSDT       6.0         0.0   

                                  asset_address  asset_decimals     usd_price  
0    0x04C154b66CB340F3Ae24111CC767e0184Ed00Cc6            18.0   2703.720000  
1    0x35fA164735182de50811E8e2E824cFb9B6118ac2            18.0   2620.870000  
2    0xc02aaa39b223fe8d0a0e5c4f27ead9083c756cc2            18.0   2627.900000  
5    0x2260FAC5E5542a773Aa44fBCfeDf7C193bc2C599             8.0  93674.970000  
6    0x2260FAC5E5542a773Aa44fBCfeDf7C193bc2C599             8.0  93674.970000  
..                                          ...             ...           ...  
115  0x35fA164735182de50811E8e2E824cFb9B6118ac2            18.0   2620.870000  
118  0x4c9EDD5852cd905f086C759E8383e09bff1E68B3            18.0      0.995400  
119  0x4c9EDD5852cd905f086C759E8383e09bff1E68B3            18.0      0.995400  
120  0x4c9EDD5852cd905f086C759E8383e09bff1E68B3            18.0      0.995400  
121  0xdAC17F958D2ee523a2206206994597C13D831ec7             6.0      0.003126  

[118 rows x 9 columns]

In [ ]:
# Initialize an empty DataFrame for combined results
all_tvl_df = pd.DataFrame()

# Loop through each SY token (using .iterrows() to loop through the DataFrame)
for _, token in tokens_df_clean.iterrows():
    address = token["sy_token"]
    name = token["name"]
    usd_price = token["usd_price"]
    decimals = token["decimals"]
    divisor = 10 ** decimals  # Set the divisor based on decimals

    # SQL query to calculate flows
    flows_query = f"""
    WITH
        flows AS (
            SELECT
                date_trunc('day', timestamp) AS stringDay,
                SUM(
                    CASE
                        WHEN inputs.arg0::String = '0x0000000000000000000000000000000000000000' THEN CAST(toUInt256(inputs.arg2::String) / {divisor} AS DOUBLE)
                        WHEN inputs.arg1::String = '0x0000000000000000000000000000000000000000' THEN - CAST(toUInt256(inputs.arg2::String) / {divisor} AS DOUBLE)
                        ELSE 0
                    END
                ) AS netFlow
            FROM
                ethereum_mainnet_decoded_logs
            WHERE
                address = evm_hex_decode('{address}')
                AND signature = 'Transfer(address,address,uint256)'
            GROUP BY
                stringDay
        )
    SELECT
        stringDay,
        SUM(netFlow) AS netFlow,
        SUM(netFlow) OVER (ORDER BY stringDay ASC) AS cum_flow
    FROM
        flows
    GROUP BY
        stringDay
    ORDER BY
        stringDay ASC
    """

    # Execute query
    try:
        flow_results = client.query_df(flows_query)

        if flow_results is not None:
            flow_results["token"] = name  # Add token name for identification
            flow_results["address"] = address  # Add token name for identification
            flow_results["netFlow"] = flow_results["netFlow"] * usd_price # Multiply netFlow by USD price
            flow_results["cum_flow"] = flow_results["cum_flow"] * usd_price # Multiply cumulative flow by USD price

            all_tvl_df = pd.concat([all_tvl_df, flow_results], ignore_index=True)
            print(f"Processed flows for {name}.")
        else:
            print(f"No flow data for {name}.")
    except Exception as e:
        print(f"Error processing {name}: {e}")

# Summarize and plot results
all_tvl_df["stringDay"] = pd.to_datetime(all_tvl_df["stringDay"])
all_tvl_df = all_tvl_df.sort_values(by="stringDay")

Processed flows for SY Autocompounding Pirex ETH.
Processed flows for SY Zircuit Ether.fi weETH.
Processed flows for SY Zircuit Staking rsETH.
Processed flows for SY Corn Lombard LBTC.
Processed flows for SY Corn Bedrock uniBTC.
Processed flows for SY Corn SolvBTC Babylon.
Processed flows for SY Corn SolvBTC Babylon.
Processed flows for SY Corn SolvBTC Babylon.
Processed flows for SY Ethena sUSDE.
Processed flows for SY Ethena USDe.
Processed flows for SY Karak USDE.
Processed flows for SY Karak sUSDe.
Processed flows for SY Mellow ENA.
Processed flows for SY Mellow sUSDe.
Processed flows for SY Corn pumpBTC.
Processed flows for SY Lombard LBTC.
Processed flows for SY Ethena USDe.
Processed flows for SY Zircuit Staking USDe.
Processed flows for SY Tensorplex Staked TAO.
Processed flows for SY ENA.
Processed flows for SY ether.fi weETH.
Processed flows for SY Staking USDS.
Processed flows for SY Staked ENA.
Processed flows for SY Staked ENA.
Processed flows for SY Syrup USDC.
Processed 

In [ ]:
data_table.DataTable(all_tvl_df, include_index=False, num_rows_per_page=20)

In [ ]:
def prepare_tvl_data(df):
    # Convert stringDay to datetime
    df['date'] = pd.to_datetime(df['stringDay'])

    # Filter for the past year
    one_year_ago = datetime.now() - timedelta(days=365)
    df_filtered = df[df['date'] >= one_year_ago].copy()

    # Calculate top 10 tokens based on maximum TVL
    top_10_tokens = df_filtered.groupby("token")["cum_flow"].max().nlargest(15).index

    # Create 'Other' category for tokens not in top 10
    df_filtered['token_category'] = df_filtered['token'].apply(
        lambda x: x if x in top_10_tokens else 'Other'
    )

    # Group by date and token_category, preserving daily data
    df_grouped = df_filtered.groupby(['date', 'token_category'])['cum_flow'].sum().reset_index()

    # Add month column for x-axis labels
    df_grouped['month'] = df_grouped['date'].dt.to_period('M').astype(str)

    return df_grouped

def create_stacked_bar_chart(df_grouped):
    # Get unique months and create datetime values for first of each month
    unique_months = sorted(df_grouped['month'].unique())
    tick_dates = pd.to_datetime([month + '-01' for month in unique_months])

    # Create stacked bar chart using plotly
    fig = px.bar(
        df_grouped,
        x='date',
        y='cum_flow',
        color='token_category',
        title='Daily Pendle TVL by Token (Past Year)',
        labels={
            'date': 'Date',
            'cum_flow_usd': 'Cumulative Flow (USD)',
            'token_category': 'Token'
        },
        height=600,
        category_orders={
            'token_category': sorted(
                df_grouped['token_category'].unique(),
                key=lambda x: float('-inf') if x == 'Other' else 1
            )
        }
    )

    # Customize layout
    fig.update_layout(
        xaxis=dict(
            tickmode='array',
            ticktext=unique_months,
            tickvals=tick_dates,
            tickangle=-45
        ),
        yaxis=dict(
            title='Cumulative Flow (USD)',
            tickformat=',.0f'  # Format large numbers with commas
        ),
        legend_title_text='Token',
        barmode='stack',
        showlegend=True,
        hovermode='x unified'
    )

    # Customize hover template
    fig.update_traces(
        hovertemplate='<b>%{x|%Y-%m-%d}</b><br>' +
                      '%{fullData.name}: $%{y:,.2f}<br>' +
                      '<extra></extra>'
    )

    return fig

# Main execution
def plot_tvl_stacked_chart(all_tvl_df):
    # Prepare the data
    df_grouped = prepare_tvl_data(all_tvl_df)

    # Create and return the figure
    fig = create_stacked_bar_chart(df_grouped)

    return fig


fig = plot_tvl_stacked_chart(all_tvl_df)
fig.show()

In [ ]:
# List of Berachain tokens to focus on
berachain_tokens = [
    "0xac614884b52dbab8728476b5d50f0d672baed31f",
    "0xaaa576f3c8b1f6f12afd37f3936ced36e1a6ab94",
    "0x14c1878bd3f989d0d2199c537ea1a6d3b5225d05",
    "0xab659cfa8a179fc305df3a083f1400e6a230bf15",
    "0xd84e88abbe6a44a2ef9b72de9def68317d6df336",
    "0xa8abe7ac0c4bb1ade8b22de6a33691fcedcbd8d3",
    "0xd7b2a47ac9236d9685b573a2428f72ec45e97c45"
]

def prepare_tvl_data(df):
    # Convert stringDay to datetime
    df['date'] = pd.to_datetime(df['stringDay'])

    # Filter for the past year
    one_year_ago = datetime.now() - timedelta(days=365)
    df_filtered = df[df['date'] >= one_year_ago].copy()

    # Filter for Berachain tokens only
    df_filtered = df_filtered[df_filtered['address'].isin(berachain_tokens)]

    # Group by date and token, summing the cumulative flow
    df_grouped = df_filtered.groupby(['date', 'token'])['cum_flow'].sum().reset_index()

    # Add month column for x-axis labels
    df_grouped['month'] = df_grouped['date'].dt.to_period('M').astype(str)

    return df_grouped

def create_stacked_bar_chart(df_grouped):
    # Get unique months and create datetime values for first of each month
    unique_months = sorted(df_grouped['month'].unique())
    tick_dates = pd.to_datetime([month + '-01' for month in unique_months])

    # Create stacked bar chart using plotly
    fig = px.bar(
        df_grouped,
        x='date',
        y='cum_flow',
        color='token',
        title='Daily TVL of Berachain SY Tokens (Past Year)',
        labels={
            'date': 'Date',
            'cum_flow_usd': 'Cumulative Flow (USD)',
            'token': 'Token'
        },
        height=600
    )

    # Customize layout
    fig.update_layout(
        xaxis=dict(
            title='Date',
            tickformat='%Y-%m-%d',  # Format the ticks as 'Year-Month-Day'
            tickangle=-45,
            showgrid=True,  # Show grid lines
            ticks="inside",  # Place ticks inside the plot
            tickmode='linear',  # Show every individual date
            tickvals=df_grouped['date'].unique()  # Use all unique dates from the dataset
        ),
        yaxis=dict(
            title='Cumulative Flow (USD)',
            tickformat=',.0f'  # Format large numbers with commas
        ),
        legend_title_text='Token',
        barmode='stack',
        showlegend=True,
        hovermode='x unified'
    )

    # Customize hover template
    fig.update_traces(
        hovertemplate='<b>%{x|%Y-%m-%d}</b><br>' +
                      '%{fullData.name}: $%{y:,.2f}<br>' +
                      '<extra></extra>'
    )

    return fig

# Main execution
def plot_tvl_stacked_chart(all_tvl_df):
    # Prepare the data
    df_grouped = prepare_tvl_data(all_tvl_df)
    print(df_grouped.head())

    # Create and return the figure
    fig = create_stacked_bar_chart(df_grouped)

    return fig


# Use this function to plot your filtered data
fig = plot_tvl_stacked_chart(all_tvl_df)
fig.show()

        date                        token      cum_flow    month
0 2025-01-07  SY Ether.Fi Liquid Bera BTC  1.265269e+05  2025-01
1 2025-01-07  SY Ether.Fi Liquid Bera ETH  7.651346e+04  2025-01
2 2025-01-08  SY Ether.Fi Liquid Bera BTC  6.315551e+06  2025-01
3 2025-01-08  SY Ether.Fi Liquid Bera ETH  8.726205e+06  2025-01
4 2025-01-09       SY Concrete USDe Vault  1.000127e+05  2025-01


In [ ]:
def prepare_tvl_data(df, filter_tokens):
    """
    Prepares the TVL data by filtering for the past year and specific token addresses.

    Parameters:
        df (pd.DataFrame): DataFrame containing TVL data.
        filter_tokens (list): List of token addresses to filter.

    Returns:
        pd.DataFrame: Processed DataFrame grouped by date and token.
    """
    # Convert stringDay to datetime
    df['date'] = pd.to_datetime(df['stringDay'])

    # Filter for the past year
    one_year_ago = datetime.now() - timedelta(days=365)
    df_filtered = df[df['date'] >= one_year_ago].copy()

    # Apply token filter
    df_filtered = df_filtered[df_filtered['address'].isin(filter_tokens)]

    # Group by date and token, summing the cumulative flow
    df_grouped = df_filtered.groupby(['date', 'token'])['cum_flow'].sum().reset_index()

    # Add month column for x-axis labels
    df_grouped['month'] = df_grouped['date'].dt.to_period('M').astype(str)

    return df_grouped

def create_stacked_bar_chart(df_grouped, title):
    """
    Creates a stacked bar chart for TVL data.

    Parameters:
        df_grouped (pd.DataFrame): Grouped TVL data.
        title (str): Title for the chart.

    Returns:
        plotly.graph_objects.Figure: Plotly figure.
    """
    # Get unique months and create datetime values for first of each month
    unique_months = sorted(df_grouped['month'].unique())
    tick_dates = pd.to_datetime([month + '-01' for month in unique_months])

    # Create stacked bar chart using Plotly
    fig = px.bar(
        df_grouped,
        x='date',
        y='cum_flow',
        color='token',
        title=title,
        labels={
            'date': 'Date',
            'cum_flow': 'Cumulative Flow (USD)',
            'token': 'Token'
        },
        height=600
    )

    # Customize layout
    fig.update_layout(
        xaxis=dict(
            title='Date',
            tickformat='%Y-%m-%d',
            tickangle=-45,
            showgrid=True,
            ticks="inside",
            tickmode='linear',
            tickvals=df_grouped['date'].unique()
        ),
        yaxis=dict(
            title='Cumulative Flow (USD)',
            tickformat=',.0f'
        ),
        legend_title_text='Token',
        barmode='stack',
        showlegend=True,
        hovermode='x unified'
    )

    # Customize hover template
    fig.update_traces(
        hovertemplate='<b>%{x|%Y-%m-%d}</b><br>' +
                      '%{fullData.name}: $%{y:,.2f}<br>' +
                      '<extra></extra>'
    )

    return fig

# Main execution function
def plot_tvl_stacked_chart(df, filter_tokens, title):
    """
    Plots the TVL stacked bar chart.

    Parameters:
        df (pd.DataFrame): DataFrame containing TVL data.
        filter_tokens (list): List of token addresses to filter.
        title (str): Title for the chart.

    Returns:
        plotly.graph_objects.Figure: Plotly figure.
    """
    df_grouped = prepare_tvl_data(df, filter_tokens)
    print(df_grouped.head())

    fig = create_stacked_bar_chart(df_grouped, title)
    return fig

# List of Berachain tokens
berachain_tokens = [
    "0xac614884b52dbab8728476b5d50f0d672baed31f",
    "0xaaa576f3c8b1f6f12afd37f3936ced36e1a6ab94",
    "0x14c1878bd3f989d0d2199c537ea1a6d3b5225d05",
    "0xab659cfa8a179fc305df3a083f1400e6a230bf15",
    "0xd84e88abbe6a44a2ef9b72de9def68317d6df336",
    "0xa8abe7ac0c4bb1ade8b22de6a33691fcedcbd8d3",
    "0xd7b2a47ac9236d9685b573a2428f72ec45e97c45"
]

# List of SuperUSD tokens
SuperUSD_tokens = [
    "0x0a91166428d71777e1a9b338b84eb9452e520b78"
]

# Use this function to plot Berachain tokens
fig_berachain = plot_tvl_stacked_chart(all_tvl_df, berachain_tokens, "Daily TVL of Berachain SY Tokens (Past Year)")
fig_berachain.show()

# Use this function to plot SuperUSD tokens
fig_superusd = plot_tvl_stacked_chart(all_tvl_df, SuperUSD_tokens, "Daily TVL of SuperUSD Tokens (Past Year)")
fig_superusd.show()


        date                        token      cum_flow    month
0 2025-01-07  SY Ether.Fi Liquid Bera BTC  1.265269e+05  2025-01
1 2025-01-07  SY Ether.Fi Liquid Bera ETH  7.651346e+04  2025-01
2 2025-01-08  SY Ether.Fi Liquid Bera BTC  6.315551e+06  2025-01
3 2025-01-08  SY Ether.Fi Liquid Bera ETH  8.726205e+06  2025-01
4 2025-01-09       SY Concrete USDe Vault  1.000127e+05  2025-01


        date         token      cum_flow    month
0 2025-02-12  SY SuperUSDC   1069.600785  2025-02
1 2025-02-13  SY SuperUSDC   7808.235992  2025-02
2 2025-02-14  SY SuperUSDC  27586.977663  2025-02
3 2025-02-15  SY SuperUSDC  39442.755923  2025-02
4 2025-02-16  SY SuperUSDC  57242.912561  2025-02
